In [1]:
import pandas as pd
import geopandas as gpd
import folium
import branca.colormap as cm
import sqlite3

In [2]:
conn = sqlite3.connect('Resources/FPA_FOD_20170508.sqlite')

In [3]:
df = pd.read_sql_query('select STATE, SUM(FIRE_SIZE) from Fires group by STATE', conn)
pd.set_option('max_columns', None)
df.head()

STATE  SUM(FIRE_SIZE)
0    AK    3.223309e+07
1    AL    9.205453e+05
2    AR    5.089118e+05
3    AZ    5.576681e+06
4    CA    1.274586e+07

In [4]:
fname = 'Resources/cb_2018_us_state_5m.shp'
nil = gpd.read_file(fname)
nil.head()

STATEFP   STATENS     AFFGEOID GEOID STUSPS          NAME LSAD  \
0      31  01779792  0400000US31    31     NE      Nebraska   00   
1      53  01779804  0400000US53    53     WA    Washington   00   
2      35  00897535  0400000US35    35     NM    New Mexico   00   
3      46  01785534  0400000US46    46     SD  South Dakota   00   
4      48  01779801  0400000US48    48     TX         Texas   00   

          ALAND       AWATER  \
0  198956658395   1371829134   
1  172112588220  12559278850   
2  314196306401    728776523   
3  196346981786   3382720225   
4  676653171537  19006305260   

                                            geometry  
0  POLYGON ((-104.05351 41.15726, -104.05267 41.2...  
1  MULTIPOLYGON (((-122.32834 48.02134, -122.3217...  
2  POLYGON ((-109.05017 31.48000, -109.04984 31.4...  
3  POLYGON ((-104.05770 44.99743, -104.05021 44.9...  
4  POLYGON ((-106.64548 31.89867, -106.64084 31.9...

In [5]:
nil=nil[['STUSPS', 'geometry']]
nil.head()

STUSPS                                           geometry
0     NE  POLYGON ((-104.05351 41.15726, -104.05267 41.2...
1     WA  MULTIPOLYGON (((-122.32834 48.02134, -122.3217...
2     NM  POLYGON ((-109.05017 31.48000, -109.04984 31.4...
3     SD  POLYGON ((-104.05770 44.99743, -104.05021 44.9...
4     TX  POLYGON ((-106.64548 31.89867, -106.64084 31.9...

In [6]:
df = df.rename(columns={
    'STATE':'STUSPS'
})
df.head()

STUSPS  SUM(FIRE_SIZE)
0     AK    3.223309e+07
1     AL    9.205453e+05
2     AR    5.089118e+05
3     AZ    5.576681e+06
4     CA    1.274586e+07

In [7]:
nilpop=nil.merge(df, on='STUSPS')
nilpop.head()

STUSPS                                           geometry  SUM(FIRE_SIZE)
0     NE  POLYGON ((-104.05351 41.15726, -104.05267 41.2...    9.673988e+05
1     WA  MULTIPOLYGON (((-122.32834 48.02134, -122.3217...    4.782218e+06
2     NM  POLYGON ((-109.05017 31.48000, -109.04984 31.4...    6.380042e+06
3     SD  POLYGON ((-104.05770 44.99743, -104.05021 44.9...    1.570866e+06
4     TX  POLYGON ((-106.64548 31.89867, -106.64084 31.9...    9.786218e+06

In [8]:
x_map = 38
y_map = -100

In [9]:
mymap = folium.Map(location=[38,-100], zoom_start=5, tiles=None)
folium.TileLayer('Stamen Terrain',control=False).add_to(mymap)
mymap

In [153]:
mymap.choropleth(
    geo_data=nilpop,
    name='Choropleth',
    data=nilpop,
    columns=['STUSPS', 'SUM(FIRE_SIZE)'],
    key_on='feature.properties.STUSPS',
    fill_color='YlOrRd',
    fill_opacity=1,
    line_opacity=0.2,
    legend_name='Total Acres Burned Per State',
    smooth_factor=0
)
mymap

C:\Users\filip\anaconda\Anaconda3\lib\site-packages\folium\folium.py:409: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  warnings.warn(


In [10]:
style_function = lambda x: {'fillColor': '#ffffff', 
                            'color':'#000000', 
                            'fillOpacity': 0.1, 
                            'weight': 0.1}
highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.50, 
                                'weight': 0.1}
NIL = folium.features.GeoJson(
    nilpop,
    style_function=style_function, 
    control=False,
    highlight_function=highlight_function, 
    tooltip=folium.features.GeoJsonTooltip(
        fields=['STUSPS', 'SUM(FIRE_SIZE)'],
        aliases=['State: ','Total Acres Burned: '],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;") 
    )
)
mymap.add_child(NIL)
mymap.keep_in_front(NIL)
folium.LayerControl().add_to(mymap)
#mymap.save('templates/choropleth_map.html')
mymap